# Imports


In [1]:
! pip install chex
! pip install evosax

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 240.4/240.4 kB 4.8 MB/s eta 0:00:00


In [2]:
import jax
import jax.numpy as jnp
import jax.scipy as jsp
import numpy as np
import chex
import typing as t
from functools import partial
import matplotlib.pyplot as plt
import json

# Video Processor

In [3]:
import os
os.environ['FFMPEG_BINARY'] = 'ffmpeg'
import moviepy.editor as mvp
from moviepy.video.io.ffmpeg_writer import FFMPEG_VideoWriter
from IPython.display import HTML, display, clear_output

class VideoWriter:
  def __init__(self, filename, fps=30.0, **kw):
    self.writer = None
    self.params = dict(filename=filename, fps=fps, **kw)

  def add(self, img):
    img = np.asarray(img)
    if self.writer is None:
      h, w = img.shape[:2]
      self.writer = FFMPEG_VideoWriter(size=(w, h), **self.params)
    if img.dtype in [np.float32, np.float64]:
      img = np.uint8(img.clip(0, 1)*255)
    if len(img.shape) == 2:
      img = np.repeat(img[..., None], 3, -1)
    self.writer.write_frame(img)

  def close(self):
    if self.writer:
      self.writer.close()

  def __enter__(self):
    return self

  def __exit__(self, *kw):
    self.close()

  def show(self, **kw):
      self.close()
      fn = self.params['filename']
      display(mvp.ipython_display(fn, **kw))

# Helper functions

In [4]:
def sigmoid(x):
    return 0.5 * (jnp.tanh(x / 2) + 1)

ker_f = lambda x, a, w, b : (b * jnp.exp( - (x[..., None] - a)**2 / w)).sum(-1)

bell = lambda x, m, s: jnp.exp(-((x-m)/s)**2 / 2)

def growth(U, m, s):
    return bell(U, m, s)*2-1

kx = jnp.array([
                [1., 0., -1.],
                [2., 0., -2.],
                [1., 0., -1.]
])
ky = jnp.transpose(kx)
def sobel_x(A):
    """
    A : (x, y, c)
    ret : (x, y, c)
    """
    return jnp.dstack([jsp.signal.convolve2d(A[:, :, c], kx, mode = 'same')
                    for c in range(A.shape[-1])])
def sobel_y(A):
    return jnp.dstack([jsp.signal.convolve2d(A[:, :, c], ky, mode = 'same')
                    for c in range(A.shape[-1])])

@jax.jit
def sobel(A):
    return jnp.concatenate((sobel_y(A)[:, :, None, :], sobel_x(A)[:, :, None, :]),
                            axis = 2)



def get_kernels(SX: int, SY: int, nb_k: int, params):
    mid = SX//2
    Ds = [ np.linalg.norm(np.mgrid[-mid:mid, -mid:mid], axis=0) /
          ((params['R']+15) * params['r'][k]) for k in range(nb_k) ]  # (x,y,k)
    K = jnp.dstack([sigmoid(-(D-1)*10) * ker_f(D, params["a"][k], params["w"][k], params["b"][k])
                    for k, D in zip(range(nb_k), Ds)])
    nK = K / jnp.sum(K, axis=(0,1), keepdims=True)
    return nK


def conn_from_matrix(mat):
    C = mat.shape[0]
    c0 = []
    c1 = [[] for _ in range(C)]
    i = 0
    for s in range(C):
        for t in range(C):
            n = mat[s, t]
            if n:
                c0 = c0 + [s]*n
                c1[t] = c1[t] + list(range(i, i+n))
            i+=n
    return c0, c1


def conn_from_lists(c0, c1, C):
    return c0, [[i == c1[i] for i in range(len(c0))] for c in range(C)]

# System Simulation Dynamics

In [5]:
class ReintegrationTracking:

    def __init__(self, SX=256, SY=256, dt=.2, dd=5, sigma=.65, border="wall", has_hidden=False,
                 hidden_dims=None, mix="softmax"):
        self.SX = SX
        self.SY = SY
        self.dt = dt
        self.dd = dd
        self.sigma = sigma
        self.has_hidden = has_hidden
        self.hidden_dims = hidden_dims
        self.border = border if border in ['wall', 'torus'] else 'wall'
        self.mix = mix

        self.apply = self._build_apply()

    def __call__(self, *args):
        return self.apply(*args)

    def _build_apply(self):

        x, y = jnp.arange(self.SX), jnp.arange(self.SY)
        X, Y = jnp.meshgrid(x, y)
        pos = jnp.dstack((Y, X)) + .5 #(SX, SY, 2)
        dxs = []
        dys = []
        dd = self.dd
        for dx in range(-dd, dd+1):
            for dy in range(-dd, dd+1):
                dxs.append(dx)
                dys.append(dy)
        dxs = jnp.array(dxs)
        dys = jnp.array(dys)
        #-----------------------------------------------------------------------------------------------
        if not self.has_hidden:

            @partial(jax.vmap, in_axes=(None, None, 0, 0))
            def step(X, mu, dx, dy):
                Xr = jnp.roll(X, (dx, dy), axis = (0, 1))
                mur = jnp.roll(mu, (dx, dy), axis = (0, 1))
                if self.border == 'torus':
                    dpmu = jnp.min(jnp.stack(
                        [jnp.absolute(pos[..., None] - (mur + jnp.array([di, dj])[None, None, :, None]))
                        for di in (-self.SX, 0, self.SX) for dj in (-self.SY, 0, self.SY)]
                    ), axis = 0)
                else :
                    dpmu = jnp.absolute(pos[..., None] - mur)
                sz = .5 - dpmu + self.sigma
                area = jnp.prod(jnp.clip(sz, 0, min(1, 2*self.sigma)) , axis = 2) / (4 * self.sigma**2)
                nX = Xr * area
                return nX

            def apply(X, F):

                ma = self.dd - self.sigma  # upper bound of the flow maggnitude
                mu = pos[..., None] + jnp.clip(self.dt * F, -ma, ma) #(x, y, 2, c) : target positions (distribution centers)
                if self.border == "wall":
                    mu = jnp.clip(mu, self.sigma, self.SX-self.sigma)
                nX = step(X, mu, dxs, dys).sum(axis = 0)

                return nX
        #-----------------------------------------------------------------------------------------------
        else :



            @partial(jax.vmap, in_axes = (None, None, None, 0, 0))
            def step_flow(X, H, mu, dx, dy):
                """Summary
                """
                Xr = jnp.roll(X, (dx, dy), axis = (0, 1))
                Hr = jnp.roll(H, (dx, dy), axis = (0, 1)) #(x, y, k)
                mur = jnp.roll(mu, (dx, dy), axis = (0, 1))

                if self.border == 'torus':
                    dpmu = jnp.min(jnp.stack(
                        [jnp.absolute(pos[..., None] - (mur + jnp.array([di, dj])[None, None, :, None]))
                        for di in (-self.SX, 0, self.SX) for dj in (-self.SY, 0, self.SY)]
                    ), axis = 0)
                else :
                    dpmu = jnp.absolute(pos[..., None] - mur)

                sz = .5 - dpmu + self.sigma
                area = jnp.prod(jnp.clip(sz, 0, min(1, 2*self.sigma)) , axis = 2) / (4 * self.sigma**2)
                nX = Xr * area
                return nX, Hr

            def apply(X, H, F):

                ma = self.dd - self.sigma  # upper bound of the flow maggnitude
                mu = pos[..., None] + jnp.clip(self.dt * F, -ma, ma) #(x, y, 2, c) : target positions (distribution centers)
                if self.border == "wall":
                    mu = jnp.clip(mu, self.sigma, self.SX-self.sigma)
                nX, nH = step_flow(X, H, mu, dxs, dys)

                if self.mix == 'avg':
                    nH = jnp.sum(nH * nX.sum(axis = -1, keepdims = True), axis = 0)
                    nX = jnp.sum(nH, axis = 0)
                    nH = nH / (nX.sum(axis = -1, keepdims = True)+1e-10)

                elif self.mix == "softmax":
                    expnX = jnp.exp(nX.sum(axis = -1, keepdims = True)) - 1
                    nX = jnp.sum(nX, axis = 0)
                    nH = jnp.sum(nH * expnX, axis = 0) / (expnX.sum(axis = 0)+1e-10) #avg rule

                elif self.mix == "stoch":
                    categorical=jax.random.categorical(
                      jax.random.PRNGKey(42),
                      jnp.log(nX.sum(axis = -1, keepdims = True)),
                      axis=0)
                    mask=jax.nn.one_hot(categorical,num_classes=(2*self.dd+1)**2,axis=-1)
                    mask=jnp.transpose(mask,(3,0,1,2))
                    nH = jnp.sum(nH * mask, axis = 0)
                    nX = jnp.sum(nX, axis = 0)

                elif self.mix == "stoch_gene_wise":
                    mask = jnp.concatenate(
                      [jax.nn.one_hot(jax.random.categorical(
                                                            jax.random.PRNGKey(42),
                                                            jnp.log(nX.sum(axis = -1, keepdims = True)),
                                                            axis=0),
                                      num_classes=(2*dd+1)**2,axis=-1)
                      for _ in range(self.hidden_dims)],
                      axis = 2)
                    mask=jnp.transpose(mask,(3,0,1,2)) # (2dd+1**2, x, y, nb_k)
                    nH = jnp.sum(nH * mask, axis = 0)
                    nX = jnp.sum(nX, axis = 0)

                return nX, nH

        return apply

# Param and Rule Space Definition

In [6]:
@chex.dataclass
class Params:
    """Flow Lenia update rule parameters
    """
    r: jnp.ndarray
    b: jnp.ndarray
    w: jnp.ndarray
    a: jnp.ndarray
    m: jnp.ndarray
    s: jnp.ndarray
    h: jnp.ndarray
    R: float

    def to_dict(self):
        return {
            "SX": self.SX,
            "SY": self.SY,
            "nb_k": self.nb_k,
            "C": self.C,
            "c0": self.c0,
            "c1": self.c1,
            "dt": self.dt,
            "dd": self.dd,
            "sigma": self.sigma,
            "n": self.n,
            "theta_A": self.theta_A,
            "border": self.border,
            "mix": self.mix
        }
    def to_json(self, path):
        with open(path, 'w') as f:
            json.dump(self.to_dict(), f)


@chex.dataclass
class CompiledParams:
    """Flow Lenia compiled parameters
    """
    fK: jnp.ndarray
    m: jnp.ndarray
    s: jnp.ndarray
    h: jnp.ndarray

    def to_dict(self):
        return {
            'fK' : self.fK.tolist(),
            'm' : self.m.tolist(),
            's' : self.s.tolist(),
            'h' : self.h.tolist()
        }

    def to_json(self, path):
        with open(path, 'w') as f:
            json.dump(self.to_dict(), f)



class RuleSpace :

    """Rule space for Flow Lenia system

    Attributes:
        kernel_keys (TYPE): Description
        nb_k (int): number of kernels of the system
        spaces (TYPE): Description
    """

    #-----------------------------------------------------------------------------
    def __init__(self, nb_k: int):
        """
        Args:
            nb_k (int): number of kernels in the update rule
        """
        self.nb_k = nb_k
        self.kernel_keys = 'r b w a m s h'.split()
        self.spaces = {
            "r" : {'low' : .2, 'high' : 1., 'mut_std' : .2, 'shape' : None},
            "b" : {'low' : .001, 'high' : 1., 'mut_std' : .2, 'shape' : (3,)},
            "w" : {'low' : .01, 'high' : .5, 'mut_std' : .2, 'shape' : (3,)},
            "a" : {'low' : .0, 'high' : 1., 'mut_std' : .2, 'shape' : (3,)},
            "m" : {'low' : .05, 'high' : .5, 'mut_std' : .2, 'shape' : None},
            "s" : {'low' : .001, 'high' : .18, 'mut_std' : .01, 'shape' : None},
            "h" : {'low' : .01, 'high' : 1., 'mut_std' : .2, 'shape' : None},
            'R' : {'low' : 2., 'high' : 25., 'mut_std' : .2, 'shape' : None},
        }
    #-----------------------------------------------------------------------------
    def sample(self, key: jnp.ndarray)->Params:
        """sample a random set of parameters

        Returns:
            Params: sampled parameters

        Args:
            key (jnp.ndarray): random generation key
        """
        kernels = {}
        for k in 'rmsh':
            key, subkey = jax.random.split(key)
            kernels[k] = jax.random.uniform(
              key=subkey, minval=self.spaces[k]['low'], maxval=self.spaces[k]['high'],
              shape=(self.nb_k,)
            )
        for k in "awb":
            key, subkey = jax.random.split(key)
            kernels[k] = jax.random.uniform(
              key=subkey, minval=self.spaces[k]['low'], maxval=self.spaces[k]['high'],
              shape=(self.nb_k, 3)
            )
        R = jax.random.uniform(key=key, minval=self.spaces['R']['low'], maxval=self.spaces['R']['high'])
        return Params(R=R, **kernels)

class KernelComputer:

    """Summary

    Attributes:
        apply (Callable): main function transforming raw params (Params) in copmiled ones (CompiledParams)
        SX (int): X size
        SY (int): Y size
    """

    def __init__(self, SX: int, SY: int, nb_k: int):
        """Summary

        Args:
            SX (int): Description
            SY (int): Description
            nb_k (int): Description
        """
        self.SX = SX
        self.SY = SY

        mid = SX // 2
        def compute_kernels(params: Params)->CompiledParams:
            """Compute kernels and return a dic containing kernels fft

            Args:
                params (Params): raw params of the system

            Returns:
                CompiledParams: compiled params which can be used as update rule
            """

            Ds = [ np.linalg.norm(np.mgrid[-mid:mid, -mid:mid], axis=0) /
                  ((params.R+15) * params.r[k]) for k in range(nb_k) ]  # (x,y,k)
            K = jnp.dstack([sigmoid(-(D-1)*10) * ker_f(D, params.a[k], params.w[k], params.b[k])
                            for k, D in zip(range(nb_k), Ds)])
            nK = K / jnp.sum(K, axis=(0,1), keepdims=True)  # Normalize kernels
            fK = jnp.fft.fft2(jnp.fft.fftshift(nK, axes=(0,1)), axes=(0,1))  # Get kernels fft

            return CompiledParams(fK=fK, m=params.m, s=params.s, h=params.h)

        self.apply = jax.jit(compute_kernels)

    def __call__(self, params: Params):
        """callback to apply
        """
        return self.apply(params)


# Flow Lenia Implementation


In [12]:
@chex.dataclass
class Config :

    """Configuration of Flow Lenia system
    """
    SX: int
    SY: int
    nb_k: int
    C: int
    c0: t.Iterable
    c1: t.Iterable
    dt: float
    dd: int = 5
    sigma: float = .65
    n: int = 2
    theta_A : float = 1.
    border: str = 'wall'

    def to_dict(self):
        return {
            'SX' : self.SX,
            'SY' : self.SY,
            'nb_k' : self.nb_k,
            'C' : self.C,
            'c0' : self.c0,
            'c1' : self.c1,
            'dt' : self.dt,
            'dd' : self.dd,
            'sigma' : self.sigma,
            'n' : self.n,
            'theta_A' : self.theta_A,
            'border' : self.border
        }


    def to_json(self, path):
        with open(path, 'w') as f:
            json.dump(self.to_dict(), f)


@chex.dataclass
class State :

    """State of the system
    """
    A: jnp.ndarray

    def to_json(self, path):
        with open(path, 'w') as f:
            json.dump(self.to_dict(), f)


@chex.dataclass
class Config_P(Config):

    """Summary
    """
    mix: str = 'stoch'
    def to_dict(self):
        return {
            "SX": self.SX,
            "SY": self.SY,
            "nb_k": self.nb_k,
            "C": self.C,
            "c0": self.c0,
            "c1": self.c1,
            "dt": self.dt,
            "dd": self.dd,
            "sigma": self.sigma,
            "n": self.n,
            "theta_A": self.theta_A,
            "border": self.border,
            "mix": self.mix
        }

@chex.dataclass
class State_P(State):

    """state of system
    """
    P: jnp.ndarray

    def to_dict(self):
        return {
            "A": self.A.tolist(),
            "P": self.P.tolist()
        }

class FlowLeniaParams:

    """Flow Lenia system with parameters embedding

    Attributes:
        config (TYPE): config of the system
        kernel_computer (TYPE): -
        rollout_fn (TYPE): -
        rule_space (TYPE): -
        step_fn (TYPE): -
    """

    #------------------------------------------------------------------------------

    def __init__(self, config: Config):
        """_

        Args:
            config (Config): config of the system
        """

        self.config = config

        self.rule_space = RuleSpace(config.nb_k)

        self.kernel_computer = KernelComputer(config.SX, config.SY, config.nb_k)

        self.RT = ReintegrationTracking(self.config.SX, self.config.SY, self.config.dt,
            self.config.dd, self.config.sigma, self.config.border, has_hidden=True,
            hidden_dims=self.config.nb_k, mix=self.config.mix)

        self.step_fn = self._build_step_fn()

        self.rollout_fn = self._build_rollout()

        self.fitness_fn = self._build_fitness_function()

    #------------------------------------------------------------------------------

    def _build_step_fn(self)->t.Callable[[State, CompiledParams], State]:
        """build step function

        Returns:
            t.Callable[[State, CompiledParams], State]: step function
        """


        SX, SY, dd, sigma, dt = (self.config.SX, self.config.SY, self.config.dd,
                             self.config.sigma, self.config.dt)

        @jax.jit
        def step(state: State, params: CompiledParams)->State:
            """
            Main step


            Args:
                state (State): state of the system where A are actications and P is the paramter map
                params (CompiledParams): compiled params of update rule

            Returns:
                State: new state of the systems
            """
            A, P = state.A, state.P
            #---------------------------Original Lenia------------------------------------
            fA = jnp.fft.fft2(A, axes=(0,1))  # (x,y,c)

            fAk = fA[:, :, self.config.c0]  # (x,y,k)

            U = jnp.real(jnp.fft.ifft2(params.fK * fAk, axes=(0,1)))  # (x,y,k)

            U = growth(U, params.m, params.s) * P # (x,y,k)

            U = jnp.dstack([ U[:, :, self.config.c1[c]].sum(axis=-1) for c in range(self.config.C) ])  # (x,y,c)

            #-------------------------------FLOW------------------------------------------

            F = sobel(U) #(x, y, 2, c) : Flow

            C_grad = sobel(A.sum(axis = -1, keepdims = True)) #(x, y, 2, 1) : concentration gradient

            alpha = jnp.clip((A[:, :, None, :]/2)**2, .0, 1.)

            F = jnp.clip(F * (1 - alpha) - C_grad * alpha, - (dd-sigma), dd - sigma)

            nA, nP = self.RT.apply(A, P, F)

            return State_P(A=nA, P=nP)

        return step

    #------------------------------------------------------------------------------

    def _build_rollout(self):
        """build a rollout function taking as input params, an initial state and a number of steps
        and returning the final state of the system and the stacked states

        Returns:
            Callable
        """
        def scan_step(carry: t.Tuple[State, CompiledParams], x)->t.Tuple[t.Tuple[State, CompiledParams], State]:
            """Summary

            Args:
                carry (t.Tuple[State, CompiledParams]): state of the system [state x params]
                x: None

            Returns:
                t.Tuple[t.Tuple[State, CompiledParams], State]: rollout function
            """
            state, params = carry
            nstate = jax.jit(self.step_fn)(state, params)
            return (nstate, params), nstate

        def rollout(params: CompiledParams, init_state: State, steps: int) -> t.Tuple[State, State]:
            """Summary

            Args:
                params (CompiledParams): compiled params of the systems
                init_state (State): initial state of the system
                steps (int): number of steps to simulate

            Returns:
                t.Tuple[State, State]: returns the final state and the stacked states of the rollout
            """
            return jax.lax.scan(scan_step, (init_state, params), None, length = steps)

        return rollout

    def _build_fitness_function(self):
        def fitness(params: CompiledParams, init_state: State, steps: int) -> jnp.ndarray:
            """Summary

            Fitness is distance of the center of mass of the initial state to the final state of the rollout.
            center of mass is bounded between [-0.5, 0.5] for both x and y axis

            """
            (final_state, _), states = self.rollout_fn(params, init_state, steps)

            x_indices, y_indices = np.indices(init_state.A.shape[:2])
            # center of mass of the initial state
            init_mass = np.sum(init_state.A, axis=-1)
            total_init_mass = np.sum(init_mass)
            x_com_init = np.sum(x_indices * init_mass) / total_init_mass
            y_com_init = np.sum(y_indices * init_mass) / total_init_mass

            # center of mass of the final state
            final_mass = np.sum(final_state.A, axis=-1)
            total_final_mass = np.sum(final_mass)
            x_com_final = np.sum(x_indices * final_mass) / total_final_mass
            y_com_final = np.sum(y_indices * final_mass) / total_final_mass

            # distance between the two centers of mass
            distance = np.sqrt((x_com_init - x_com_final)**2 + (y_com_init - y_com_final)**2)
            # normalize the distance
            return distance





        return fitness


In [8]:
#@title Conversion Utils
def state2img_P(A, P):
    return jnp.sum(A, axis=-1, keepdims=True) * P[..., :3]

# Parameter Reshaping Class

In [9]:
from evosax import ParameterReshaper
class FlowReshaper(ParameterReshaper):

    def __init__(self, config, fl):
        self.config = config
        self.fl = fl

    def flatten(self, params):
        min_clip = []
        max_clip = []
        r = params.r.ravel()  # Flatten r
        b = params.b.ravel()  # Flatten b
        w = params.w.ravel()  # Flatten w
        a = params.a.ravel()  # Flatten a
        m = params.m.ravel()  # Assuming m needs to be a flat array
        s = params.s.ravel()  # Assuming s needs to be a flat array
        h = params.h.ravel()  # Assuming h needs to be a flat array
        R = np.array([params.R])  # Keep R as a scalar encapsulated in an array
        """
        if return_clips:
            min_clip+= [self.fl.rule_space.spaces['r']['low']]*len(r)
            max_clip+= [self.fl.rule_space.spaces['r']['high']]*len(r)
            min_clip+= [self.fl.rule_space.spaces['b']['low']]*len(b)
            max_clip+= [self.fl.rule_space.spaces['b']['high']]*len(b)
            min_clip+= [self.fl.rule_space.spaces['w']['low']]*len(w)
            max_clip+= [self.fl.rule_space.spaces['w']['high']]*len(w)
            min_clip+= [self.fl.rule_space.spaces['a']['low']]*len(a)
            max_clip+= [self.fl.rule_space.spaces['a']['high']]*len(a)
            min_clip+= [self.fl.rule_space.spaces['m']['low']]*len(m)
            max_clip+= [self.fl.rule_space.spaces['m']['high']]*len(m)
            min_clip+= [self.fl.rule_space.spaces['s']['low']]*len(s)
            max_clip+= [self.fl.rule_space.spaces['s']['high']]*len(s)
            min_clip+= [self.fl.rule_space.spaces['h']['low']]*len(h)
            max_clip+= [self.fl.rule_space.spaces['h']['high']]*len(h)
            min_clip+= [self.fl.rule_space.spaces['R']['low']]
            max_clip+= [self.fl.rule_space.spaces['R']['high']]
            min_clip = np.array(min_clip)
            max_clip = np.array(max_clip)
            return np.concatenate([r, b, w, a, m, s, h, R]), min_clip, max_clip
          """
        return np.concatenate([r, b, w, a, m, s, h, R])


    def reshape(self, flat_params):
        r = flat_params[:self.config.nb_k]
        # clip r to be between low and high defined in the config
        r = np.clip(r, self.fl.rule_space.spaces['r']['low'], self.fl.rule_space.spaces['r']['high'])

        b = flat_params[self.config.nb_k:3*self.config.nb_k]
        b = np.clip(b, self.fl.rule_space.spaces['b']['low'], self.fl.rule_space.spaces['b']['high'])

        w = flat_params[3*self.config.nb_k:5*self.config.nb_k]
        w = np.clip(w, self.fl.rule_space.spaces['w']['low'], self.fl.rule_space.spaces['w']['high'])

        a = flat_params[5*self.config.nb_k:7*self.config.nb_k]
        a = np.clip(a, self.fl.rule_space.spaces['a']['low'], self.fl.rule_space.spaces['a']['high'])

        m = flat_params[7*self.config.nb_k:8*self.config.nb_k]
        m = np.clip(m, self.fl.rule_space.spaces['m']['low'], self.fl.rule_space.spaces['m']['high'])

        s = flat_params[8*self.config.nb_k:9*self.config.nb_k]
        s = np.clip(s, self.fl.rule_space.spaces['s']['low'], self.fl.rule_space.spaces['s']['high'])

        h = flat_params[9*self.config.nb_k:10*self.config.nb_k]
        h = np.clip(h, self.fl.rule_space.spaces['h']['low'], self.fl.rule_space.spaces['h']['high'])

        R = flat_params[-1]
        R = np.clip(R, self.fl.rule_space.spaces['R']['low'], self.fl.rule_space.spaces['R']['high'])

        return Params(r=r, b=b, w=w, a=a, m=m, s=s, h=h, R=R)

# Initialization

In [10]:
from evosax import OpenES, FitnessShaper

rng = jax.random.PRNGKey(0)
number_of_kernels = 10 #@param {type:"raw"}
nb_k = number_of_kernels
world_size = 256
SX = SY = world_size
C = 2 # @param {type : "integer"}
dt = 0.2 # @param
theta_A = 2.0 # @param
sigma = 0.65 #@param
M = np.ones((C, C), dtype=int) * nb_k
print(M)


nb_k = int(M.sum())
print(nb_k)
mixing_rule = 'stoch' #@param {type : 'string'}
c0, c1 = conn_from_matrix( M )
config = Config_P(SX=SX, SY=SY, nb_k=nb_k, C=C,
                  c0=c0, c1=c1, dt=.2, theta_A=2.,
                  mix=mixing_rule)
fl = FlowLeniaParams(config)
roll_fn = jax.jit(fl.rollout_fn, static_argnums=(2,))
reshaper = FlowReshaper(config, fl)
params = fl.rule_space.sample(rng)
flattened_params = reshaper.flatten(params)

pop_size = 16 #@param {type:"raw"}

es = OpenES(
    popsize=pop_size, num_dims=len(flattened_params), pholder_params=flattened_params, sigma_init=sigma, lrate_init=0.01, maximize=True)
es_params = es.default_params

es_state = es.initialize(rng)
es_state = es_state.replace(best_fitness=0.)

mx, my = SX//2, SY//2 # center coordinated
state_seed, param_seed = jax.random.split(rng)
A0 = jnp.zeros((SX, SY, C)).at[mx-20:mx+20, my-20:my+20, :].set(
    jax.random.uniform(state_seed, (40, 40, C))
)
P0 = jnp.ones((SX, SY, nb_k)) * jax.random.uniform(param_seed, (1, 1, nb_k))
state = State_P(A=A0, P=P0)


[[10 10]
 [10 10]]
40
ParameterReshaper: 521 parameters detected for optimization.


# Evolving the Parameters

In [11]:
# 50
generations_per_cycle = 50
cycles = 60
for cycle in range(cycles):
  for gen in range(generations_per_cycle):
      fitnesses = []
      rng, key = jax.random.split(rng)
      new_params, es_state = es.ask(key, es_state, es_params)
      for i in range(pop_size):
          params = reshaper.reshape(new_params[i, :])
          compiled_params = fl.kernel_computer(params)
          fitness = fl.fitness_fn(compiled_params, state, 400)
          print('fitness:', fitness)
          fitnesses.append(fitness)
      fitnesses = jnp.stack(fitnesses)
      print('Generation:', gen+cycle*generations_per_cycle, 'Fitnesses:', fitnesses)
      es_state = es.tell(new_params, fitnesses, es_state, es_params)
      best_fitness = es_state.best_fitness
      print('best Fitness: ', best_fitness)
      best_params = reshaper.reshape(es_state.best_member)

      best_compiled_params = fl.kernel_computer(best_params)
  T = 500 #@param {type : 'integer'}
  (final_state, _), states = roll_fn(best_compiled_params, state, T)

  with VideoWriter("example.mp4", 60) as vid:
      for i in range(T):
          vid.add(state2img_P(states.A[i], states.P[i]))
      vid.show(width = 360, heigth = 360)

fitness: 0.36690286
fitness: 0.22481595
fitness: 0.18414345
fitness: 0.9879352
fitness: 0.776329
fitness: 0.057540417
fitness: 0.023162678
fitness: 0.11993845
fitness: 1.4851019
fitness: 0.37095112
fitness: 0.13430268
fitness: 0.31479648
fitness: 0.2184137
fitness: 0.97848034
fitness: 0.44224685
fitness: 0.18092814
Generation: 0 Fitnesses: [0.36690286 0.22481595 0.18414345 0.9879352  0.776329   0.05754042
 0.02316268 0.11993845 1.4851019  0.37095112 0.13430268 0.31479648
 0.2184137  0.97848034 0.44224685 0.18092814]
best Fitness:  1.4851019
fitness: 0.21783416
fitness: 0.883442
fitness: 0.0723984
fitness: 0.5290375
fitness: 0.097914025
fitness: 0.108944856
fitness: 0.07724332
fitness: 0.15694793
fitness: 0.16633381
fitness: 0.067609735
fitness: 0.27972305
fitness: 0.3100978
fitness: 0.54118496
fitness: 0.2389505
fitness: 0.13621536
fitness: 0.104854845
Generation: 1 Fitnesses: [0.21783416 0.883442   0.0723984  0.5290375  0.09791403 0.10894486
 0.07724332 0.15694793 0.16633381 0.0676097

fitness: 0.4832067
fitness: 1.0021935
fitness: 0.202535
fitness: 1.6373343
fitness: 0.13847125
fitness: 0.5213562
fitness: 0.26071033
fitness: 0.2759333
fitness: 0.5626703
fitness: 1.3727118
fitness: 0.20581724
fitness: 1.4403524
fitness: 0.28765583
fitness: 0.3657476
fitness: 0.46344608
fitness: 0.13524324
Generation: 50 Fitnesses: [0.4832067  1.0021935  0.202535   1.6373343  0.13847125 0.5213562
 0.26071033 0.2759333  0.5626703  1.3727118  0.20581724 1.4403524
 0.28765583 0.3657476  0.46344608 0.13524324]
best Fitness:  5.2088437
fitness: 0.4215364
fitness: 0.2834858
fitness: 0.47867003
fitness: 0.63760924
fitness: 0.23752226
fitness: 0.38852164
fitness: 0.39937
fitness: 0.514624
fitness: 0.22800519
fitness: 0.4116137
fitness: 0.37227732
fitness: 0.051893704
fitness: 1.1784352
fitness: 0.3283344
fitness: 0.37863687
fitness: 0.8796356
Generation: 51 Fitnesses: [0.4215364  0.2834858  0.47867003 0.63760924 0.23752226 0.38852164
 0.39937    0.514624   0.22800519 0.4116137  0.37227732 0.0

fitness: 1.035045
fitness: 0.726103
fitness: 2.4991405
fitness: 0.31858012
fitness: 3.3301356
fitness: 0.23782122
fitness: 1.1406164
fitness: 0.06449066
fitness: 3.7638307
fitness: 0.14436617
fitness: 0.5771774
fitness: 1.1144158
fitness: 0.048670765
fitness: 0.55112845
fitness: 0.39457217
fitness: 0.883787
Generation: 100 Fitnesses: [1.035045   0.726103   2.4991405  0.31858012 3.3301356  0.23782122
 1.1406164  0.06449066 3.7638307  0.14436617 0.5771774  1.1144158
 0.04867077 0.55112845 0.39457217 0.883787  ]
best Fitness:  5.3755813
fitness: 2.2056084
fitness: 0.5636975
fitness: 0.36241698
fitness: 0.30490854
fitness: 0.41078275
fitness: 0.67959875
fitness: 0.52540237
fitness: 0.5498923
fitness: 0.21180305
fitness: 0.023125177
fitness: 0.636641
fitness: 1.1593527
fitness: 0.5826217
fitness: 0.3964615
fitness: 1.9248832
fitness: 1.927877
Generation: 101 Fitnesses: [2.2056084  0.5636975  0.36241698 0.30490854 0.41078275 0.67959875
 0.52540237 0.5498923  0.21180305 0.02312518 0.636641   

fitness: 2.0205395
fitness: 0.45609924
fitness: 0.28374755
fitness: 0.6666131
fitness: 0.9402744
fitness: 0.121779576
fitness: 0.9738691
fitness: 0.14756054
fitness: 1.9720944
fitness: 0.11650218
fitness: 0.30748302
fitness: 1.0512588
fitness: 0.35571298
fitness: 0.35162166
fitness: 0.90511775
fitness: 0.5095639
Generation: 150 Fitnesses: [2.0205395  0.45609924 0.28374755 0.6666131  0.9402744  0.12177958
 0.9738691  0.14756054 1.9720944  0.11650218 0.30748302 1.0512588
 0.35571298 0.35162166 0.90511775 0.5095639 ]
best Fitness:  6.652608
fitness: 0.98879087
fitness: 0.14445452
fitness: 0.2250369
fitness: 1.8692565
fitness: 0.31267044
fitness: 0.4259615
fitness: 0.14664356
fitness: 0.032136127
fitness: 0.6015884
fitness: 0.40761703
fitness: 0.31125903
fitness: 0.21146606
fitness: 2.1413965
fitness: 1.5252442
fitness: 2.5960066
fitness: 0.62583184
Generation: 151 Fitnesses: [0.98879087 0.14445452 0.2250369  1.8692565  0.31267044 0.4259615
 0.14664356 0.03213613 0.6015884  0.40761703 0.31

fitness: 0.21832186
fitness: 0.22772965
fitness: 3.707884
fitness: 0.022676693
fitness: 2.4872565
fitness: 0.07192771
fitness: 0.19401173
fitness: 0.7734587
fitness: 0.7530928
fitness: 1.3472298
fitness: 0.41966283
fitness: 0.7926757
fitness: 1.0543419
fitness: 0.7642489
fitness: 0.24420296
fitness: 0.80205
Generation: 200 Fitnesses: [0.21832186 0.22772965 3.707884   0.02267669 2.4872565  0.07192771
 0.19401173 0.7734587  0.7530928  1.3472298  0.41966283 0.7926757
 1.0543419  0.7642489  0.24420296 0.80205   ]
best Fitness:  8.092549
fitness: 0.48519903
fitness: 0.80616415
fitness: 0.72695726
fitness: 1.0574573
fitness: 0.9481875
fitness: 0.1106789
fitness: 1.0068022
fitness: 0.8300977
fitness: 0.46354452
fitness: 0.3133331
fitness: 5.6061063
fitness: 0.42829818
fitness: 0.9562224
fitness: 0.8621834
fitness: 2.2189467
fitness: 0.63289225
Generation: 201 Fitnesses: [0.48519903 0.80616415 0.72695726 1.0574573  0.9481875  0.1106789
 1.0068022  0.8300977  0.46354452 0.3133331  5.6061063  0.

...

fitness: 4.946872
fitness: 9.570756
fitness: 3.3723924
fitness: 25.43521
fitness: 21.62552
fitness: 27.21293
fitness: 35.95701
fitness: 34.798195
fitness: 8.54381
fitness: 9.711633
fitness: 3.5360165
fitness: 21.71689
fitness: 24.517797
fitness: 22.882673
fitness: 2.979936
fitness: 30.641283
Generation: 1400 Fitnesses: [ 4.946872   9.570756   3.3723924 25.43521   21.62552   27.21293
 35.95701   34.798195   8.54381    9.711633   3.5360165 21.71689
 24.517797  22.882673   2.979936  30.641283 ]
best Fitness:  70.05846
fitness: 34.376472
fitness: 22.562637
fitness: 28.415472
fitness: 37.000004
fitness: 8.1254015
fitness: 3.453449
fitness: 39.03089
fitness: 30.316578
fitness: 38.803764
fitness: 15.838598
fitness: 7.8480964
fitness: 15.025751
fitness: 4.3710575
fitness: 43.33644
fitness: 19.354025
fitness: 21.06879
Generation: 1401 Fitnesses: [34.376472  22.562637  28.415472  37.000004   8.1254015  3.453449
 39.03089   30.316578  38.803764  15.838598   7.8480964 15.025751
  4.3710575 43.3364

fitness: 19.425434
fitness: 44.35994
fitness: 42.339405
fitness: 39.789177
fitness: 1.2069387
fitness: 2.144401
fitness: 14.4702425
fitness: 3.6153164
fitness: 5.745438
fitness: 9.119555
fitness: 42.50959
fitness: 32.17996
fitness: 19.306837
fitness: 9.898504
fitness: 23.085072
fitness: 4.908321
Generation: 1450 Fitnesses: [19.425434  44.35994   42.339405  39.789177   1.2069387  2.144401
 14.4702425  3.6153164  5.745438   9.119555  42.50959   32.17996
 19.306837   9.898504  23.085072   4.908321 ]
best Fitness:  70.05846
fitness: 32.896656
fitness: 40.543278
fitness: 6.7980022
fitness: 30.815058
fitness: 26.524221
fitness: 19.189268
fitness: 46.168674
fitness: 18.261127
fitness: 1.8977377
fitness: 6.5181246
fitness: 48.89964
fitness: 33.354256
fitness: 6.4765477
fitness: 2.8657558
fitness: 34.28233
fitness: 45.302666
Generation: 1451 Fitnesses: [32.896656  40.543278   6.7980022 30.815058  26.524221  19.189268
 46.168674  18.261127   1.8977377  6.5181246 48.89964   33.354256
  6.4765477 

fitness: 14.33651
fitness: 11.729806
fitness: 8.518116
fitness: 8.556567
fitness: 44.0797
fitness: 48.745735
fitness: 25.566359
fitness: 2.4784825
fitness: 8.234031
fitness: 14.371186
fitness: 50.83857
fitness: 44.547302
fitness: 44.19134
fitness: 31.924145
fitness: 37.72901
fitness: 35.061996
Generation: 1500 Fitnesses: [14.33651   11.729806   8.518116   8.556567  44.0797    48.745735
 25.566359   2.4784825  8.234031  14.371186  50.83857   44.547302
 44.19134   31.924145  37.72901   35.061996 ]
best Fitness:  77.74698
fitness: 17.373009
fitness: 42.052868
fitness: 7.9989657
fitness: 16.395733
fitness: 4.418726
fitness: 31.56189
fitness: 2.9191065
fitness: 24.622232
fitness: 16.597921
fitness: 6.018936
fitness: 12.039851
fitness: 2.3089664
fitness: 4.842136
fitness: 28.21707
fitness: 7.327807
fitness: 10.454934
Generation: 1501 Fitnesses: [17.373009  42.052868   7.9989657 16.395733   4.418726  31.56189
  2.9191065 24.622232  16.597921   6.018936  12.039851   2.3089664
  4.842136  28.21

fitness: 53.06582
fitness: 11.994426
fitness: 9.562077
fitness: 2.854376
fitness: 1.733
fitness: 32.079407
fitness: 2.8107839
fitness: 41.77741
fitness: 22.259758
fitness: 8.939862
fitness: 49.706867
fitness: 54.422516
fitness: 39.229843
fitness: 21.792341
fitness: 34.59467
fitness: 18.83193
Generation: 1550 Fitnesses: [53.06582   11.994426   9.562077   2.854376   1.733     32.079407
  2.8107839 41.77741   22.259758   8.939862  49.706867  54.422516
 39.229843  21.792341  34.59467   18.83193  ]
best Fitness:  77.74698
fitness: 3.4874732
fitness: 49.111053
fitness: 14.3351
fitness: 15.523807
fitness: 36.44745
fitness: 7.8141823
fitness: 47.62523
fitness: 59.063793
fitness: 7.011078
fitness: 1.2247212
fitness: 46.706753
fitness: 47.559196
fitness: 2.755563
fitness: 12.580967
fitness: 34.153927
fitness: 41.960754
Generation: 1551 Fitnesses: [ 3.4874732 49.111053  14.3351    15.523807  36.44745    7.8141823
 47.62523   59.063793   7.011078   1.2247212 46.706753  47.559196
  2.755563  12.580

KeyboardInterrupt: 

In [ ]:
#@title Save Best Params
from google.colab import drive
import numpy as np
drive.mount('/drive')
np.savetxt(best_params.to_json(f'/drive/My Drive/LeniaEvolutions/{best_fitness}_params.txt'))
